In [1]:
from concurrent.futures import ThreadPoolExecutor
import glob
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.metrics import average_precision_score
import torch
from torch import nn, optim
from torch.utils.data import DataLoader, Dataset
from torch.utils.tensorboard import SummaryWriter
from tqdm.autonotebook import tqdm
from torch.nn.utils.rnn import pack_padded_sequence, pad_packed_sequence, pad_sequence
from collections import Counter
import pickle
import torch.nn.functional as F

from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.preprocessing import StandardScaler
from torch.optim.lr_scheduler import LinearLR

C:\Users\pnaka\AppData\Local\Temp\ipykernel_13972\4146715127.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm


In [2]:
device = "cuda" if torch.cuda.is_available() else "cpu"
device

'cuda'

In [3]:
NUM_TAGS = 256 # Max number of tags
EMBEDDING_SIZE = 768 # dimension one embedding
ENC_NUM_HEADS = 2 # number of heads of encoder
ENC_NUM_LAYERS = 2 # number of layer in encoder 
LATENT_SIZE = EMBEDDING_SIZE # dimension of latent representation of series of embeddings
CLASSIFIER_DEPTH = [LATENT_SIZE//4, LATENT_SIZE//4, LATENT_SIZE//8, LATENT_SIZE//8, LATENT_SIZE//16, LATENT_SIZE//16] # layer sizes for classifier
ATTENTION_DIM = NUM_TAGS # dimension of attention, which gathers predictions for binary classifiers
ATTENTION_HEADS = 4
BATCH_SIZE = 32
EPOCHS = 10
WEIGHT_DECAY = 0 #1e-5
LR = 0.0001
CLIP_NORM = 1.0
DO_CLIP_NORM = False

# DATA PREP

In [4]:
# Load train and test data from CSV files
df_train = pd.read_csv('train.csv')
df_test = pd.read_csv('test.csv')

In [5]:
# Prepare training and validation data
df_train, df_val = train_test_split(df_train, test_size=0.05, random_state=42)

In [6]:
# Functions to load and process data
def get_track_idx(filename):
    return int(filename.split('\\')[-1].split('.')[0])

def load_and_count_embeds(fn):
    embeds = np.load(fn)
    track_idx = get_track_idx(fn)
    return track_idx, embeds.shape[0], embeds

In [7]:
scaler = StandardScaler()

In [8]:
# Load embeddings from .npy files
print("Loading embeddings...")
file_list = glob.glob('track_embeddings/*.npy')
track_idx2embeds = {}
with ThreadPoolExecutor() as executor:
    for track_idx, num_embeds, embeds in tqdm(executor.map(load_and_count_embeds, file_list), total=len(file_list)):
        track_idx2embeds[track_idx] = embeds
        scaler = scaler.partial_fit(embeds)

Loading embeddings...


  0%|          | 0/76714 [00:00<?, ?it/s]

In [9]:
def calculate_class_weights(train_data, num_tags):
    tag_counter = Counter()
    total_tags = 0

    for track_idx, embeds, tags in train_data:
        tag_counter.update(tags)
        total_tags += len(tags)
        
    class_weights = np.zeros(num_tags)
    for tag, count in tag_counter.items():
        class_weights[tag] = 1 / (count / total_tags)
        
    return class_weights

In [10]:
def prepare_data(df):
    all_data = []
    for index, row in tqdm(df.iterrows(), "Processing dataset", total=len(df)):
        track_idx = row['track']
        embed = np.array(track_idx2embeds[track_idx], dtype=np.float32)
        embed = scaler.transform(embed)
        tags = list(map(int, row['tags'].split(','))) if 'tags' in row and pd.notnull(row['tags']) else []
        all_data.append((track_idx, embed, tags))
    return all_data

train_data = prepare_data(df_train)
val_data = prepare_data(df_val)
test_data = prepare_data(df_test)
class_weights = calculate_class_weights(train_data, NUM_TAGS)

Processing dataset:   0%|          | 0/48577 [00:00<?, ?it/s]

Processing dataset:   0%|          | 0/2557 [00:00<?, ?it/s]

Processing dataset:   0%|          | 0/25580 [00:00<?, ?it/s]

In [11]:
class EmbeddingDataset(Dataset):
    def __init__(self, data, num_tags, device):
        self.data = data
        self.num_tags = num_tags
        self.device = device

    def __len__(self):
        return len(self.data)

    def __getitem__(self, index):
        track_id = self.data[index][0]
        embeds = torch.tensor(self.data[index][1], dtype=torch.float32).to(self.device)
        tags = torch.zeros(self.num_tags, dtype=torch.float32).to(self.device)
        if len(self.data[index][2]) > 0:
            tags[self.data[index][2]] = 1
        return track_id, embeds, tags

# MODEL

In [12]:
class EncoderModel(nn.Module):
    def __init__(self, embedding_size, num_heads, num_layers, latent_size, to_device):
        super(EncoderModel, self).__init__()
        self.embedding_size = embedding_size
        self.num_heads = num_heads
        self.num_layers = num_layers
        self.latent_size = latent_size

        encoder_layer = nn.TransformerEncoderLayer(d_model=self.embedding_size, nhead=self.num_heads, 
                                                   device=to_device, dtype=torch.float32)
        self.transformer_encoder = nn.TransformerEncoder(encoder_layer, num_layers=self.num_layers)
        self.out_proj = nn.Linear(self.embedding_size, self.latent_size, device=to_device, dtype=torch.float32)

    def forward(self, x, attention_mask):
        # x shape: (seq_len, batch_size, embedding_size)
        x = self.transformer_encoder(x, src_key_padding_mask=attention_mask)  # (seq_len, batch_size, embedding_size)
        return self.out_proj(x[-1])

class MLPClassifier(nn.Module):
    def __init__(self, input_dim, hidden_dims, output_dim, to_device):
        super(MLPClassifier, self).__init__()
        
        layers = []
        
        # Input layer
        layers.append(nn.Linear(input_dim, hidden_dims[0], dtype=torch.float32, device=to_device))
        layers.append(nn.Tanh())
        layers.append(nn.BatchNorm1d(hidden_dims[0], dtype=torch.float32, device=to_device))
        #layers.append(nn.Dropout(0.05))
        
        # Hidden layers
        for i in range(len(hidden_dims) - 1):
            layers.append(nn.Linear(hidden_dims[i], hidden_dims[i+1], device=to_device))
            layers.append(nn.Tanh())
            layers.append(nn.BatchNorm1d(hidden_dims[i+1], dtype=torch.float32, device=to_device))
            #layers.append(nn.Dropout(0.05))
            
        # Output layer
        layers.append(nn.Linear(hidden_dims[-1], output_dim, dtype=torch.float32, device=to_device))
        
        self.model = nn.Sequential(*layers)
    
    def forward(self, x):
        return self.model(x)
        
class MultiClassifierModel(nn.Module):
    def __init__(self, latent_size, classifier_depth, num_tags, to_device):
        super(MultiClassifierModel, self).__init__()
        self.classifiers = nn.ModuleList([
            MLPClassifier(latent_size, classifier_depth, 1, to_device) for _ in range(num_tags)
        ])

    def forward(self, x):
        outputs = [classifier(x) for i, classifier in enumerate(self.classifiers)]
        return torch.cat(outputs, dim=1)

class OrchestratorModel(nn.Module):
    def __init__(self, embedding_size, enc_num_heads, enc_num_layers, latent_size, classifier_depth, attention_dim, attention_heads, num_tags, to_device):
        super(OrchestratorModel, self).__init__()
        self.encoder = EncoderModel(embedding_size, enc_num_heads, enc_num_layers, latent_size, to_device)
        self.bn = nn.BatchNorm1d(latent_size, dtype=torch.float32, device=to_device)
        self.decoder = MultiClassifierModel(latent_size, classifier_depth, num_tags, to_device)
        self.cross_attention = nn.MultiheadAttention(attention_dim, num_heads=attention_heads, dtype=torch.float32, device=to_device)
        self.out_proj = nn.Linear(attention_dim, num_tags, dtype=torch.float32, device=to_device)
        self.q_proj = nn.Linear(latent_size, attention_dim, dtype=torch.float32, device=to_device)
        self.k_proj = nn.Linear(latent_size + num_tags, attention_dim, dtype=torch.float32, device=to_device)
        self.v_proj = nn.Linear(latent_size + num_tags, attention_dim, dtype=torch.float32, device=to_device)        

    def forward(self, x, src_attention_mask):
        # Encoder output
        latent_representation = self.encoder(x, src_attention_mask)  # [Batch, Latent]
        latent_representation = self.bn(latent_representation) # [Batch, Latent]
        
        # Decoder output
        initial_preds = self.decoder(latent_representation)  # [Batch, Num_tags]

        # note: we detach here, so only classifiers would affect the way latent_representation is learned during the training
        combined_input = torch.cat((latent_representation.detach(), initial_preds.detach()), dim=1) # [Batch, Latent + Num_tags]
        
        # Preparing Q, K, V for attention
        # Query: the latents we receive ("Ask about latents")
        Q = self.q_proj(latent_representation.detach()).unsqueeze(0)  # [1, Batch, Attention_Dim]
        # Key: the latents themselves plus predictions from binary classifiers ("what to pay attention to")
        K = self.k_proj(combined_input).unsqueeze(0) # [1, Batch, Attention_Dim]
        # Values: latents + predictions ("what to choose from and weight on")
        V = self.v_proj(combined_input).unsqueeze(0)  # [1, Batch, Attention_Dim]

        # Multi-head attention
        attn_output, _ = self.cross_attention(Q, K, V)  # [1, Batch, Attention_dim]

        # Fully connected layer to produce probabilities
        x = self.out_proj(attn_output.squeeze(0))  # [Batch, Num_tags]
        
        return x, initial_preds

In [13]:
def save_checkpoint(model, main_optimizer, main_scheduler, classifier_optimizers, classifier_schedulers, epoch, filename='checkpoint.pth'):
    checkpoint = {
        'model_state_dict': model.state_dict(),
        'optimizer_state_dict': main_optimizer.state_dict(),
        'scheduler_state_dict': main_scheduler.state_dict(),
        'epoch': epoch,
        'scaler': scaler,
        'num_classifiers': len(classifier_optimizers)
    }
    for i, (optimizer, scheduler) in enumerate(zip(classifier_optimizers, classifier_schedulers)):
        checkpoint[f'classifier_optimizer_{i}_state_dict'] = optimizer.state_dict()
        checkpoint[f'classifier_scheduler_{i}_state_dict'] = scheduler.state_dict()
    torch.save(checkpoint, filename)

def load_checkpoint(filename, model, main_optimizer, main_scheduler, classifier_optimizers, classifier_schedulers):
    # Load the checkpoint
    checkpoint = torch.load(filename)
    # Load the model state
    model.load_state_dict(checkpoint['model_state_dict'])
    
    # Load the main optimizer and scheduler state
    main_optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
    main_scheduler.load_state_dict(checkpoint['scheduler_state_dict'])
    
    # Load the classifier optimizers and schedulers
    num_classifiers = checkpoint['num_classifiers']
    for i in range(num_classifiers):
        classifier_optimizers[i].load_state_dict(checkpoint[f'classifier_optimizer_{i}_state_dict'])
        classifier_schedulers[i].load_state_dict(checkpoint[f'classifier_scheduler_{i}_state_dict'])
    
    # Load the epoch number
    epoch = checkpoint['epoch']
    
    return epoch

# TRAIN, VAL, PRED SETUP

In [14]:
def collate_for_tails(x):
    # makes a batch of at least 2 samples to handle tails
    return x + x if len(x)<2 else x

In [15]:
import gc
torch.cuda.empty_cache()
gc.collect()

380

In [16]:
train_loader = DataLoader(EmbeddingDataset(train_data, NUM_TAGS, device), 
                          batch_size=BATCH_SIZE, shuffle=True, collate_fn=collate_for_tails)
val_loader = DataLoader(EmbeddingDataset(val_data, NUM_TAGS, device), 
                        batch_size=BATCH_SIZE, shuffle=False, collate_fn=collate_for_tails)
test_loader = DataLoader(EmbeddingDataset(test_data, NUM_TAGS, device), 
                         batch_size=BATCH_SIZE, shuffle=False, collate_fn=collate_for_tails)

In [17]:
model = OrchestratorModel(EMBEDDING_SIZE, ENC_NUM_HEADS, ENC_NUM_LAYERS, LATENT_SIZE, CLASSIFIER_DEPTH, ATTENTION_DIM, ATTENTION_HEADS, NUM_TAGS, device)

In [18]:
# Main optimizer for the OrchestratorModel without MultiClassifierModel
main_parameters = [param for name, param in model.named_parameters() if 'decoder.classifiers' not in name]
#main_optimizer = optim.Adam(main_parameters, lr=LR, weight_decay=WEIGHT_DECAY)
main_optimizer = optim.Adam(main_parameters, lr=LR, weight_decay=WEIGHT_DECAY)

# Individual optimizers for each MLPClassifier
classifier_parameters = [classifier.parameters() for classifier in model.decoder.classifiers]
#classifier_optimizers = [optim.Adam(parameters, lr=LR, weight_decay=WEIGHT_DECAY) for parameters in classifier_parameters]
classifier_optimizers = [optim.Adam(parameters, lr=LR, weight_decay=WEIGHT_DECAY) for parameters in classifier_parameters]

# Create class weights for each tag
class_weights_list = [torch.tensor(class_weights[tag_idx], dtype=torch.float32).to(device) for tag_idx in range(NUM_TAGS)]

# Loss functions
criterion = nn.BCEWithLogitsLoss(pos_weight=torch.tensor(class_weights, dtype=torch.float32)).to(device)
classifier_criterions = [nn.BCEWithLogitsLoss(pos_weight=class_weights_list[i]).to(device) for i in range(NUM_TAGS)]

main_scheduler = LinearLR(main_optimizer, start_factor=1.0, end_factor=0.0001, total_iters=EPOCHS)
classifier_schedulers = [LinearLR(optimizer, start_factor=1.0, end_factor=0.0001, total_iters=EPOCHS) for optimizer in classifier_optimizers]

In [19]:
def train_model(model, dataloader, epoch):
    model.train()
    main_total_loss = 0.0
    classifier_total_losses = [0] * len(classifier_parameters)
    pbar = tqdm(enumerate(dataloader), desc="Train batch", total=len(dataloader))
    
    for i, batch in pbar:
        x = [item[1] for item in batch]
        y = torch.stack([item[2] for item in batch]).to(device)
        
        lengths = torch.tensor([len(seq) for seq in x], dtype=torch.int64).to('cpu')
        x_padded = pad_sequence(x, batch_first=True, padding_value=0).to(device)
        mask = torch.zeros(x_padded.shape[:2], dtype=torch.bool).to(device)
        for idx, length in enumerate(lengths):
            mask[idx, :length] = 1
        mask = mask.logical_not().to(device)

        main_optimizer.zero_grad()
        for opt in classifier_optimizers:
            opt.zero_grad()
            
        outputs, initial_preds = model(x_padded.transpose(0, 1), mask)
        
        # Compute the loss for the main model parts (encoder, attention, etc.)
        loss = criterion(outputs, y.float())
        
        # Compute individual losses for each MLPClassifier
        classifier_losses = [classifier_criterions[i](outputs[:, i], y[:, i]) 
                             for i in tqdm(range(NUM_TAGS), desc="Classifiers loss", leave=False)]        
        # Backpropagate the loss for the main model parts
        loss.backward(retain_graph=True)
        if DO_CLIP_NORM: 
            torch.nn.utils.clip_grad_norm_(main_parameters, CLIP_NORM)
        main_optimizer.step()

        cls_loss_stats = {}
        # Backpropagate individual losses for each MLPClassifier
        for idx, cls_loss in tqdm(enumerate(classifier_losses), 
                                  desc="Classifiers backprop", 
                                  total=len(classifier_losses), 
                                  leave=False):
            classifier_total_losses[idx] += cls_loss.item() 
            cls_loss_stats[f"tag_{idx}"] = cls_loss.item() 
            retain_grad_graph = idx < (len(classifier_losses)-1) # retain up until the last one
            cls_loss.backward(retain_graph=retain_grad_graph)
            if DO_CLIP_NORM: 
                torch.nn.utils.clip_grad_norm_(classifier_parameters[idx], CLIP_NORM)
            classifier_optimizers[idx].step()

        writer.add_scalars('Classifier losses', cls_loss_stats, epoch * len(dataloader) + i)        
        
        # Aggregate total loss for logging
        total_classifier_loss = sum(classifier_losses)
        full_loss = loss.item() + total_classifier_loss.item()
        main_total_loss += loss.item()
        
        current_lr = main_optimizer.param_groups[0]['lr']
        lr_stats = {"main": main_optimizer.param_groups[0]['lr']}
        for idx, optimizer in enumerate(classifier_optimizers):
            lr_stats[f"tag_{idx}"] = optimizer.param_groups[0]['lr']
        writer.add_scalars('Learning rates', lr_stats, epoch * len(dataloader) + i)        
        writer.add_scalars('Training Losses', 
                          {
                                "full": full_loss, 
                                "MHA": loss.item(),
                                "TotalBCLoss": total_classifier_loss.item(),
                                "MeanBCLoss": total_classifier_loss.item() / NUM_TAGS
                          }, epoch * len(dataloader) + i)
        pbar.set_postfix({"full_loss":full_loss, "loss_mha":loss.item(), "loss_bc":total_classifier_loss.item(), "main_lr":current_lr})
        
    # Step the scheduler
    main_scheduler.step()
    for idx, cls_scheduler in tqdm(enumerate(classifier_schedulers),
                                   total=len(classifier_schedulers),
                                   desc="Optimizers step", leave=False):
        cls_scheduler.step()

In [20]:
# Validation Function
def validate_model(model, dataloader, epoch):
    model.eval()
    total_loss = 0.0
    all_avg_precision = []
    pbar = tqdm(enumerate(dataloader), desc="Validation batch", total=len(dataloader))

    with torch.no_grad():
        for i, batch in pbar:
            x = [item[1] for item in batch]
            y = torch.stack([item[2] for item in batch]).to(device)
            
            lengths = torch.tensor([len(seq) for seq in x], dtype=torch.int64).to('cpu')
            x_padded = pad_sequence(x, batch_first=True, padding_value=0).to(device)
            
            mask = torch.zeros(x_padded.shape[:2], dtype=torch.bool).to(device)
            for idx, length in enumerate(lengths):
                mask[idx, :length] = 1
            mask = mask.logical_not().to(device)

            outputs, _ = model(x_padded.transpose(0, 1), mask)
            
            # Compute the loss for the main model parts (encoder, attention, etc.)
            loss = criterion(outputs, y.float())
            
            # Compute individual losses for each MLPClassifier
            classifier_losses = [classifier_criterions[i](outputs[:, i], y[:, i]) for i in range(NUM_TAGS)]

            # Aggregate total loss for logging
            total_classifier_loss = sum(classifier_losses)
            full_loss = loss.item() + total_classifier_loss.item()
            total_loss += full_loss
            
            for y_true, y_pred in zip(y.cpu().numpy(), outputs.cpu().numpy()):
                avg_precision = average_precision_score(y_true, y_pred)
                all_avg_precision.append(avg_precision)
                
            pbar.set_postfix({"val_loss": total_loss / (i+1), "avg_precision": np.mean(all_avg_precision) if all_avg_precision else 0})
    
    avg_loss = total_loss / len(dataloader)
    avg_precision = np.mean(all_avg_precision)
    writer.add_scalar('Validation Loss', avg_loss, epoch)
    writer.add_scalar('Validation Average Precision', avg_precision, epoch)
    
    return avg_loss, avg_precision

In [21]:
def predict_model(model, dataloader, sample_count):
    model.eval()
    
    df_predictions = pd.DataFrame(columns=["track", "prediction"])
    
    with torch.no_grad():
        for i, batch in tqdm(enumerate(dataloader), desc="Prediction batch", total=len(dataloader)):
            x = [item[1] for item in batch]
            track_ids = [item[0] for item in batch]

            lengths = torch.tensor([len(seq) for seq in x], dtype=torch.int64).to('cpu')
            x_padded = pad_sequence(x, batch_first=True, padding_value=0).to(device)
            
            mask = torch.zeros(x_padded.shape[:2], dtype=torch.bool).to(device)
            for idx, length in enumerate(lengths):
                mask[idx, :length] = 1
            mask = mask.logical_not().to(device)

            outputs, _ = model(x_padded.transpose(0, 1), mask)
            
            predictions = torch.sigmoid(outputs).cpu().numpy()

            # Create a temporary DataFrame for this batch
            batch_df = pd.DataFrame({
                "track": track_ids,
                "prediction": [",".join(map(str, predictions[idx])) for idx in range(len(track_ids))]
            })

            # Append the temporary DataFrame to the main DataFrame
            df_predictions = pd.concat([df_predictions, batch_df], ignore_index=True)

    return df_predictions.iloc[:sample_count]

# TRAIN AND VALIDATION

In [22]:
writer = SummaryWriter()

In [23]:
# To resume training or evaluation later, use the following:
# start_epoch, loaded_scaler = load_checkpoint(model, optimizer, scheduler, 'best_checkpoint.pth')

In [ ]:
# Main Loop
best_val_loss = float('inf')
start_epoch = 0
pbar = tqdm(range(start_epoch, EPOCHS), desc="Epoch")
for epoch in pbar:
    train_model(model, train_loader, epoch)
    val_loss, val_avg_precision = validate_model(model, val_loader, epoch)
    print(f"Epoch {epoch+1}, Validation Loss: {val_loss}, Validation Average Precision: {val_avg_precision}")
    save_checkpoint(model, main_optimizer, main_scheduler, classifier_optimizers, classifier_schedulers, epoch, f'runs/checkpoint_e{epoch}.pth')
    df_predictions = predict_model(model, test_loader, len(test_data))
    df_predictions.to_csv(f"predictions_{epoch}.csv", index=False)    
    if val_loss < best_val_loss:
        best_val_loss = val_loss
        save_checkpoint(model, main_optimizer, main_scheduler, classifier_optimizers, classifier_schedulers, epoch, f'runs/checkpoint_best.pth')
print("Done training.")

Epoch:   0%|          | 0/10 [00:00<?, ?it/s]

Train batch:   0%|          | 0/1519 [00:00<?, ?it/s]

Classifiers loss:   0%|          | 0/256 [00:00<?, ?it/s]

Classifiers backprop:   0%|          | 0/256 [00:00<?, ?it/s]

Classifiers loss:   0%|          | 0/256 [00:00<?, ?it/s]

...

Classifiers backprop:   0%|          | 0/256 [00:00<?, ?it/s]

Classifiers loss:   0%|          | 0/256 [00:00<?, ?it/s]

Classifiers backprop:   0%|          | 0/256 [00:00<?, ?it/s]

Classifiers loss:   0%|          | 0/256 [00:00<?, ?it/s]

Classifiers backprop:   0%|          | 0/256 [00:00<?, ?it/s]

# PREDICTION

In [ ]:
val_loss, val_avg_precision = validate_model(model, val_loader, epoch)

In [ ]:
# Predictions
df_predictions = predict_model(model, test_loader, len(test_data))

In [ ]:
# Save to CSV
df_predictions.to_csv("predictions.csv", index=False)

In [ ]:
print("DONE!")

In [ ]:
val_loss, val_avg_precision = validate_model(model, val_loader, epoch)